In [1]:
%load_ext autoreload
%autoreload 2

In [127]:
import pandas as pd
from regime_ml.data.common.loaders import load_dataframe
from regime_ml.utils.config import load_configs
from regime_ml.regimes.hmm import HMMRegimeDetector
from regime_ml.features.macro.selection import get_top_features

In [206]:
macro_cfg = load_configs()["macro_data"]["regime_universe"]
feat_path = macro_cfg["raw_features_path"]

In [313]:
df_feat = load_dataframe(feat_path)
df_feat = df_feat.dropna() # drop burn-in period

In [300]:
split_date = '2019-01-01'

df_train = df_selected.loc[:split_date]
X_train = df_train.values
feature_names = df_train.columns.to_list()

df_test = df_selected.loc[split_date:]
X_test = df_test.values

X_full = df_selected.values

In [309]:
# --Initialisation--
n_regimes = 5
covariance_type = 'full'

# 1. Emission Initialisation
from regime_ml.regimes.hmm import initialise_emissions
init_means, init_covars, scaler = initialise_emissions(df_train, n_clusters=n_regimes, covariance_type=covariance_type)

# 2. Transition Initialisation
from regime_ml.regimes.hmm import initialise_transitions
init_transmat = initialise_transitions(n_regimes=n_regimes, p_stay=0.9)

# 3. Initial State Probabilities 
from regime_ml.regimes.hmm import initialise_probabilities
init_startprob = initialise_probabilities(n_regimes=n_regimes)

init_covars.shape

(5, 8, 8)

In [ ]:
from regime_ml.regimes.hmm import initialise_emissions
from regime_ml.regimes.hmm import initialise_transitions
from regime_ml.regimes.hmm import initialise_probabilities

fitted_models = {}
for n_features in range(5, 15):
    selected_features = get_top_features(n=n_features)
    df_feat_selected = df_feat[selected_features]
    feature_names = df_feat_selected.columns

    for split_date in ['2019-01-01', '2020-01-01', '2021-01-01']:
        df_train = df_feat_selected.loc[:split_date]
        X_train = df_train.values
    
        for n_regimes in range(3, 5):
            init_startprob = initialise_probabilities(n_regimes=n_regimes)

            for covariance_type in ['full', 'diag']:
                init_means, init_covars, scaler = initialise_emissions(df_train, n_clusters=n_regimes, covariance_type=covariance_type)

                for p_stay in [0.9, 0.95, 0.99]:
                    init_transmat = initialise_transitions(n_regimes=n_regimes, p_stay=p_stay)

                    model = HMMRegimeDetector(
                        n_regimes=n_regimes,
                        covariance_type=covariance_type,
                        startprob=init_startprob,
                        transmat=init_transmat,
                        means=init_means,
                        covars=init_covars,
                        feature_names=feature_names, # type: ignore
                        scaler=scaler
                    )

                    X_train_scaled = scaler.fit_transform(X_train)
                    fitted_model = model.fit(X_train_scaled)
                    fitted_models[f"(Feats:{n_features})_(Split:{split_date})_(Regimes:{n_regimes})_(CovType:{covariance_type})_(PStay:{p_stay})"] = fitted_model

fitted_models

{'(Feats:5)_(Split:2019-01-01)_(Regimes:3)_(CovType:full)_(PStay:0.9)': HMMRegimeDetector(is_fitted=True),
 '(Feats:5)_(Split:2019-01-01)_(Regimes:3)_(CovType:full)_(PStay:0.95)': HMMRegimeDetector(is_fitted=True),
 '(Feats:5)_(Split:2019-01-01)_(Regimes:3)_(CovType:full)_(PStay:0.99)': HMMRegimeDetector(is_fitted=True),
 '(Feats:5)_(Split:2019-01-01)_(Regimes:3)_(CovType:diag)_(PStay:0.9)': HMMRegimeDetector(is_fitted=True),
 '(Feats:5)_(Split:2019-01-01)_(Regimes:3)_(CovType:diag)_(PStay:0.95)': HMMRegimeDetector(is_fitted=True),
 '(Feats:5)_(Split:2019-01-01)_(Regimes:3)_(CovType:diag)_(PStay:0.99)': HMMRegimeDetector(is_fitted=True),
 '(Feats:5)_(Split:2019-01-01)_(Regimes:4)_(CovType:full)_(PStay:0.9)': HMMRegimeDetector(is_fitted=True),
 '(Feats:5)_(Split:2019-01-01)_(Regimes:4)_(CovType:full)_(PStay:0.95)': HMMRegimeDetector(is_fitted=True),
 '(Feats:5)_(Split:2019-01-01)_(Regimes:4)_(CovType:full)_(PStay:0.99)': HMMRegimeDetector(is_fitted=True),
 '(Feats:5)_(Split:2019-01-01)_

In [312]:
from regime_ml.regimes.visualisation import plot_regime_timeseries
from regime_ml.regimes.visualisation import plot_ticker_by_regime

fig1 = plot_ticker_by_regime('SPY', df_selected.index, regimes)
fig1.show()

fig2 = plot_regime_timeseries(df_selected, regimes, proba)
fig2.show()